# FIFA World Cup 2022 - Simulation

## Libraries

In [16]:
import numpy as np
import pandas as pd
from matplotlib import pyplot as plt
import seaborn as sns
import datetime
from sklearn import linear_model
from sklearn import ensemble
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix, roc_curve, roc_auc_score
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import PolynomialFeatures
from sklearn.model_selection import GridSearchCV
from tqdm import tqdm
from itertools import combinations
from sklearn import tree
import random
import statistics
from sklearn import linear_model
from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.model_selection import cross_val_score
from sklearn.ensemble import RandomForestClassifier
from sklearn import tree
from sklearn.impute import KNNImputer

## Read Data:

In [18]:
data = pd.read_csv('data/international_matches.csv')

In [19]:
data

date       home_team     away_team home_team_continent  \
0      1993-08-08         Bolivia       Uruguay       South America   
1      1993-08-08          Brazil        Mexico       South America   
2      1993-08-08         Ecuador     Venezuela       South America   
3      1993-08-08          Guinea  Sierra Leone              Africa   
4      1993-08-08        Paraguay     Argentina       South America   
...           ...             ...           ...                 ...   
23916  2022-06-14         Moldova       Andorra              Europe   
23917  2022-06-14   Liechtenstein        Latvia              Europe   
23918  2022-06-14           Chile         Ghana       South America   
23919  2022-06-14           Japan       Tunisia                Asia   
23920  2022-06-14  Korea Republic         Egypt                Asia   

      away_team_continent  home_team_fifa_rank  away_team_fifa_rank  \
0           South America                   59                   22   
1           North America                    8                   14   
2           South America                   35                   94   
3                  Africa                   65                   86   
4           South America                   67                    5   
...                   ...                  ...                  ...   
23916              Europe                  180                  153   
23917              Europe                  192                  135   
23918              Africa                   28                   60   
23919              Africa                   23                   35   
23920              Africa                   29                   32   

       home_team_total_fifa_points  away_team_total_fifa_points  \
0                                0                            0   
1                                0                            0   
2                                0                            0   
3                                0                            0   
4                                0                            0   
...                            ...                          ...   
23916                          932                         1040   
23917                          895                         1105   
23918                         1526                         1387   
23919                         1553                         1499   
23920                         1519                         1500   

       home_team_score  ...  shoot_out home_team_result  \
0                    3  ...         No              Win   
1                    1  ...         No             Draw   
2                    5  ...         No              Win   
3                    1  ...         No              Win   
4                    1  ...         No             Lose   
...                ...  ...        ...              ...   
23916                2  ...         No              Win   
23917                0  ...         No             Lose   
23918                0  ...        Yes             Lose   
23919                0  ...         No             Lose   
23920                4  ...         No              Win   

      home_team_goalkeeper_score away_team_goalkeeper_score  \
0                            NaN                        NaN   
1                            NaN                        NaN   
2                            NaN                        NaN   
3                            NaN                        NaN   
4                            NaN                        NaN   
...                          ...                        ...   
23916                       65.0                        NaN   
23917                        NaN                       65.0   
23918                       79.0                       74.0   
23919                       73.0                        NaN   
23920                       75.0                        NaN   

       home_team_mean_defense_score 

## Data Preprocessing:

### Missing Values:

In [20]:
data.isna().sum()

date                                 0
home_team                            0
away_team                            0
home_team_continent                  0
away_team_continent                  0
home_team_fifa_rank                  0
away_team_fifa_rank                  0
home_team_total_fifa_points          0
away_team_total_fifa_points          0
home_team_score                      0
away_team_score                      0
tournament                           0
city                                 0
country                              0
neutral_location                     0
shoot_out                            0
home_team_result                     0
home_team_goalkeeper_score       15542
away_team_goalkeeper_score       15826
home_team_mean_defense_score     16134
home_team_mean_offense_score     15411
home_team_mean_midfield_score    15759
away_team_mean_defense_score     16357
away_team_mean_offense_score     15609
away_team_mean_midfield_score    15942
dtype: int64

### Matches from 2010:

In [21]:
data = data[data['date'] > '2009-12-31']
#data



#data = data[-data.isna().any(axis=1)]
data

date       home_team   away_team home_team_continent  \
12911  2010-01-02         IR Iran   Korea DPR                Asia   
12912  2010-01-02           Qatar        Mali                Asia   
12913  2010-01-02           Syria    Zimbabwe                Asia   
12914  2010-01-02           Yemen  Tajikistan                Asia   
12915  2010-01-03          Angola      Gambia              Africa   
...           ...             ...         ...                 ...   
23916  2022-06-14         Moldova     Andorra              Europe   
23917  2022-06-14   Liechtenstein      Latvia              Europe   
23918  2022-06-14           Chile       Ghana       South America   
23919  2022-06-14           Japan     Tunisia                Asia   
23920  2022-06-14  Korea Republic       Egypt                Asia   

      away_team_continent  home_team_fifa_rank  away_team_fifa_rank  \
12911                Asia                   64                   86   
12912              Africa                   86                   47   
12913              Africa                   91                  109   
12914                Asia                  130                  165   
12915              Africa                   95                  116   
...                   ...                  ...                  ...   
23916              Europe                  180                  153   
23917              Europe                  192                  135   
23918              Africa                   28                   60   
23919              Africa                   23                   35   
23920              Africa                   29                   32   

       home_team_total_fifa_points  away_team_total_fifa_points  \
12911                            0                            0   
12912                            0                            0   
12913                            0                            0   
12914                            0                            0   
12915                            0                            0   
...                            ...                          ...   
23916                          932                         1040   
23917                          895                         1105   
23918                         1526                         1387   
23919                         1553                         1499   
23920                         1519                         1500   

       home_team_score  ...  shoot_out home_team_result  \
12911                1  ...         No              Win   
12912                0  ...         No             Draw   
12913                6  ...         No              Win   
12914                0  ...         No             Lose   
12915                1  ...         No             Draw   
...                ...  ...        ...              ...   
23916                2  ...         No              Win   
23917                0  ...         No             Lose   
23918                0  ...        Yes             Lose   
23919                0  ...         No             Lose   
23920                4  ...         No              Win   

      home_team_goalkeeper_score away_team_goalkeeper_score  \
12911                        NaN                        NaN   
12912                        NaN                       53.0   
12913                        NaN                        NaN   
12914                        NaN                        NaN   
12915                       70.0                       67.0   
...                          ...                        ...   
23916                       65.0                        NaN   
23917                        NaN                       65.0   
23918                       79.0                       74.0   
23919                       73.0                        NaN   
23920                       75.0                        NaN   

       home_team_mean_defense_score home_team_mean_offense_s

### Teams in World Cup:

In [22]:
Teams =  ["Qatar", "Ecuador", "Senegal", "Netherlands", "IR Iran", "Wales", "USA", "England", "Argentina", "Saudi Arabia", "Mexico", "Poland", "France", "Australia", "Denmark", "Tunisia", "Spain", "Germany", "Costa Rica", "Japan", "Belgium", "Canada", "Morocco", "Croatia", "Morocco", "Croatia", "Brazil", "Serbia", "Switzerland", "Cameroon", "Portugal", "Ghana", "Uruguay", "Korea Republic"]

In [23]:
data = data[data['home_team'].isin(Teams) | data['away_team'].isin(Teams)]

idx_home = data['home_team'][data.index]
idx_away = data['away_team'][data.index]

In [24]:
X, y = data.loc[:,['home_team_fifa_rank', 'away_team_fifa_rank',
       'home_team_total_fifa_points', 'away_team_total_fifa_points', 'home_team_goalkeeper_score',	'away_team_goalkeeper_score',	'home_team_mean_defense_score',	'home_team_mean_offense_score',	'home_team_mean_midfield_score',	'away_team_mean_defense_score',	'away_team_mean_offense_score',	'away_team_mean_midfield_score', 'neutral_location']], data['home_team_result']




In [25]:
idx_1 = X["home_team_total_fifa_points"] == 0
X.loc[idx_1==True, "home_team_total_fifa_points"] =  np.nan

idx_2 = X["away_team_total_fifa_points"] == 0
X.loc[idx_2==True, "away_team_total_fifa_points"] =  np.nan


X

home_team_fifa_rank  away_team_fifa_rank  home_team_total_fifa_points  \
12911                   64                   86                          NaN   
12912                   86                   47                          NaN   
12918                   34                   99                          NaN   
12924                  104                   21                          NaN   
12926                  110                   64                          NaN   
...                    ...                  ...                          ...   
23908                   10                   18                       1658.0   
23909                   26                    2                       1544.0   
23918                   28                   60                       1526.0   
23919                   23                   35                       1553.0   
23920                   29                   32                       1519.0   

       away_team_total_fifa_points  home_team_goalkeeper_score  \
12911                          NaN                         NaN   
12912                          NaN                         NaN   
12918                          NaN                        66.0   
12924                          NaN                         NaN   
12926                          NaN                         NaN   
...                            ...                         ...   
23908                       1588.0                        81.0   
23909                       1827.0                        87.0   
23918                       1387.0                        79.0   
23919                       1499.0                        73.0   
23920                       1500.0                        75.0   

       away_team_goalkeeper_score  home_team_mean_defense_score  \
12911                         NaN                           NaN   
12912                        53.0                           NaN   
12918                         NaN                          71.8   
12924                        79.0                           NaN   
12926                         NaN                           NaN   
...                           ...                           ...   
23908                        74.0                          85.2   
23909                        89.0                          75.2   
23918                        74.0                          75.5   
23919                         NaN                          75.2   
23920                         NaN                          73.0   

       home_team_mean_offense_score  home_team_mean_midfield_score  \
12911                           NaN                            NaN   
12912                           NaN                            NaN   
12918                          73.3                           80.2   
12924                           NaN                            NaN   
12926                           NaN                            NaN   
...                             ...                            ...   
23908                          83.0                           83.5   
23909                          84.7                           75.8   
23918                          76.7                           78.2   
23919                          75.0                           77.5   
23920                          80.0                           73.8   

       away_team_mean_defense_score  away_team_mean_offense_score  \
12911                           NaN                           NaN   
12912                          73.0                          74.7   
12918                           NaN                           NaN   
12924                          73.8                          76.0   
12926                           NaN                           NaN   
...                             ...                           ...   
23908                          75.0                          73.0   
23909                          80.8                    

In [26]:
imputer = KNNImputer(n_neighbors=10)
new_values = imputer.fit_transform(X)


X = pd.DataFrame(new_values)
#X = X.set_index(idx_teams)

X

0     1       2       3     4     5      6      7      8      9   \
0      64.0  86.0   946.0   842.3  72.7  71.0  71.87  72.60  73.97  72.26   
1      86.0  47.0   418.3   602.1  71.9  53.0  69.20  71.85  72.28  73.00   
2      34.0  99.0  1036.3   691.2  66.0  66.6  71.80  73.30  80.20  68.07   
3     104.0  21.0   676.1  1147.0  69.4  79.0  67.59  65.94  69.35  73.80   
4     110.0  64.0   312.1   532.1  69.4  73.9  69.14  70.20  71.43  73.42   
...     ...   ...     ...     ...   ...   ...    ...    ...    ...    ...   
4077   10.0  18.0  1658.0  1588.0  81.0  74.0  85.20  83.00  83.50  75.00   
4078   26.0   2.0  1544.0  1827.0  87.0  89.0  75.20  84.70  75.80  80.80   
4079   28.0  60.0  1526.0  1387.0  79.0  74.0  75.50  76.70  78.20  75.50   
4080   23.0  35.0  1553.0  1499.0  73.0  74.9  75.20  75.00  77.50  70.80   
4081   29.0  32.0  1519.0  1500.0  75.0  75.3  73.00  80.00  73.80  73.23   

         10     11   12  
0     73.32  69.82  1.0  
1     74.70  77.80  0.0  
2     70.94  70.43  1.0  
3     76.00  75.00  0.0  
4     74.17  75.01  0.0  
...     ...    ...  ...  
4077  73.00  78.50  0.0  
4078  85.70  85.50  0.0  
4079  76.00  78.20  1.0  
4080  72.30  74.00  0.0  
4081  79.30  70.80  0.0  

[4082 rows x 13 columns]

In [27]:
X.columns = ['home_team_fifa_rank', 'away_team_fifa_rank', 'home_team_total_fifa_points',
             'away_team_total_fifa_points', 'home_team_goalkeeper_score', 'away_team_goalkeeper_score',
             'home_team_mean_defense_score', 'home_team_mean_offense_score', 'home_team_mean_midfield_score',
             'away_team_mean_defense_score', 'away_team_mean_offense_score', 'away_team_mean_midfield_score',
             'neutral_location']

X


home_team_fifa_rank  away_team_fifa_rank  home_team_total_fifa_points  \
0                    64.0                 86.0                        946.0   
1                    86.0                 47.0                        418.3   
2                    34.0                 99.0                       1036.3   
3                   104.0                 21.0                        676.1   
4                   110.0                 64.0                        312.1   
...                   ...                  ...                          ...   
4077                 10.0                 18.0                       1658.0   
4078                 26.0                  2.0                       1544.0   
4079                 28.0                 60.0                       1526.0   
4080                 23.0                 35.0                       1553.0   
4081                 29.0                 32.0                       1519.0   

      away_team_total_fifa_points  home_team_goalkeeper_score  \
0                           842.3                        72.7   
1                           602.1                        71.9   
2                           691.2                        66.0   
3                          1147.0                        69.4   
4                           532.1                        69.4   
...                           ...                         ...   
4077                       1588.0                        81.0   
4078                       1827.0                        87.0   
4079                       1387.0                        79.0   
4080                       1499.0                        73.0   
4081                       1500.0                        75.0   

      away_team_goalkeeper_score  home_team_mean_defense_score  \
0                           71.0                         71.87   
1                           53.0                         69.20   
2                           66.6                         71.80   
3                           79.0                         67.59   
4                           73.9                         69.14   
...                          ...                           ...   
4077                        74.0                         85.20   
4078                        89.0                         75.20   
4079                        74.0                         75.50   
4080                        74.9                         75.20   
4081                        75.3                         73.00   

      home_team_mean_offense_score  home_team_mean_midfield_score  \
0                            72.60                          73.97   
1                            71.85                          72.28   
2                            73.30                          80.20   
3                            65.94                          69.35   
4                            70.20                          71.43   
...                            ...                            ...   
4077                         83.00                          83.50   
4078                         84.70                          75.80   
4079                         76.70                          78.20   
4080                         75.00                          77.50   
4081                         80.00                          73.80   

      away_team_mean_defense_score  away_team_mean_offense_score  \
0                            72.26                         73.32   
1                            73.00                         74.70   
2                            68.07                         70.94   
3                            73.80                         76.00   
4                            73.42                         74.17   
...                            ...                           ...   
4077                         75.00                         73.00   
4078                         80.80                         85.70   
4079                         75.50        

In [28]:
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, random_state=20)

In [29]:
X_test

home_team_fifa_rank  away_team_fifa_rank  home_team_total_fifa_points  \
501                  56.0                 67.0                        735.6   
2462                  8.0                 17.0                       1266.0   
1826                 14.0                 65.0                       1056.0   
739                   5.0                 98.0                       1189.0   
808                  12.0                  8.0                        976.0   
...                   ...                  ...                          ...   
3528                 31.0                144.0                       1499.0   
3771                 94.0                 28.0                       1244.0   
3189                 57.0                 29.0                       1394.0   
3679                  3.0                 58.0                       1761.0   
171                   4.0                  2.0                       1398.7   

      away_team_total_fifa_points  home_team_goalkeeper_score  \
501                         672.0                        69.0   
2462                       1049.0                        84.0   
1826                        523.0                        79.0   
739                         342.0                        81.0   
808                        1052.0                        86.0   
...                           ...                         ...   
3528                       1072.0                        73.0   
3771                       1515.0                        69.0   
3189                       1496.0                        69.0   
3679                       1401.0                        87.0   
171                        1504.7                        83.0   

      away_team_goalkeeper_score  home_team_mean_defense_score  \
501                         75.0                         67.20   
2462                        80.0                         83.20   
1826                        68.0                         71.50   
739                         70.0                         82.00   
808                         74.0                         82.50   
...                          ...                           ...   
3528                        63.9                         73.71   
3771                        80.0                         68.50   
3189                        72.0                         78.20   
3679                        76.0                         84.20   
171                         90.0                         77.80   

      home_team_mean_offense_score  home_team_mean_midfield_score  \
501                           75.3                          67.50   
2462                          86.7                          83.50   
1826                          72.3                          71.80   
739                           86.3                          82.50   
808                           84.7                          84.00   
...                            ...                            ...   
3528                          74.7                          77.11   
3771                          71.0                          69.80   
3189                          80.0                          80.00   
3679                          88.3                          86.80   
171                           83.7                          83.80   

      away_team_mean_defense_score  away_team_mean_offense_score  \
501                          70.20                         75.70   
2462                         78.80                         80.70   
1826                         68.80                         69.30   
739                          65.20                         72.70   
808                          76.00                         80.00   
...                            ...                           ...   
3528                         69.67                         70.64   
3771                         75.80                         80.30   
3189                         73.20        

### Divide Home and Away datasets:

In [30]:
home = X.loc[:,['home_team_fifa_rank',
       'home_team_total_fifa_points', 'home_team_goalkeeper_score',	'home_team_mean_defense_score',	'home_team_mean_offense_score',	'home_team_mean_midfield_score']], data['home_team_result']



home = home[0].set_index(idx_home)
home_team_df = home.groupby('home_team').mean()

home_team_df


home_team_fifa_rank  home_team_total_fifa_points  \
home_team                                                       
Afghanistan           139.500000                   639.500000   
Albania                53.588235                   791.941176   
Algeria                43.000000                   976.891667   
Andorra               169.777778                   405.000000   
Angola                 96.666667                   400.100000   
...                          ...                          ...   
Vietnam               105.166667                  1060.133333   
Wales                  36.546875                  1077.560937   
Yemen                 149.375000                   347.250000   
Zambia                 65.000000                   652.680000   
Zimbabwe              108.250000                   631.850000   

             home_team_goalkeeper_score  home_team_mean_defense_score  \
home_team                                                               
Afghanistan                   71.250000                     71.220000   
Albania                       74.470588                     71.205882   
Algeria                       70.041667                     75.875000   
Andorra                       68.722222                     70.225556   
Angola                        63.366667                     65.332222   
...                                 ...                           ...   
Vietnam                       67.100000                     68.976667   
Wales                         74.218750                     75.251563   
Yemen                         69.487500                     69.882500   
Zambia                        72.550000                     70.540000   
Zimbabwe                      70.075000                     66.065000   

             home_team_mean_offense_score  home_team_mean_midfield_score  
home_team                                                                 
Afghanistan                     71.440000                      71.135000  
Albania                         69.311765                      71.370588  
Algeria                         78.250000                      77.991667  
Andorra                         70.685556                      70.138889  
Angola                          70.922222                      69.204444  
...                                   ...                            ...  
Vietnam                         70.456667                      70.916667  
Wales                           73.365625                      78.381250  
Yemen                           70.951250                      71.725000  
Zambia                          70.772000                      72.324000  
Zimbabwe                        69.725000                      66.020000  

[184 rows x 6 columns]

In [31]:
away = X.loc[:,['away_team_fifa_rank',
       'away_team_total_fifa_points', 'away_team_goalkeeper_score',	'away_team_mean_defense_score',	'away_team_mean_offense_score',	'away_team_mean_midfield_score']], data['home_team_result']


away = away[0].set_index([idx_away])
away_team_df = away.groupby('away_team').mean()

away_team_df


away_team_fifa_rank  away_team_total_fifa_points  \
away_team                                                       
Afghanistan           150.000000                   624.500000   
Albania                59.142857                   864.885714   
Algeria                36.800000                  1107.208000   
Andorra               173.400000                   464.920000   
Angola                 95.800000                   714.900000   
...                          ...                          ...   
Vietnam               118.500000                   705.333333   
Wales                  32.788462                  1098.194231   
Yemen                 148.500000                   612.250000   
Zambia                 75.818182                   798.436364   
Zimbabwe              107.833333                   744.166667   

             away_team_goalkeeper_score  away_team_mean_defense_score  \
away_team                                                               
Afghanistan                   63.600000                     67.345000   
Albania                       75.571429                     72.322857   
Algeria                       72.900000                     75.696000   
Andorra                       66.910000                     68.463000   
Angola                        67.940000                     69.292000   
...                                 ...                           ...   
Vietnam                       64.683333                     69.273333   
Wales                         74.134615                     75.526923   
Yemen                         64.875000                     69.078750   
Zambia                        70.290909                     70.190909   
Zimbabwe                      68.050000                     67.743333   

             away_team_mean_offense_score  away_team_mean_midfield_score  
away_team                                                                 
Afghanistan                     69.900000                      67.680000  
Albania                         69.457143                      71.171429  
Algeria                         78.028000                      77.252000  
Andorra                         70.582000                      68.637000  
Angola                          69.560000                      65.308000  
...                                   ...                            ...  
Vietnam                         71.161667                      69.091667  
Wales                           73.819231                      78.046154  
Yemen                           70.667500                      68.933750  
Zambia                          69.928182                      71.233636  
Zimbabwe                        68.266667                      69.205000  

[186 rows x 6 columns]

### Models:

- Decision Tree:

In [32]:
param_grid = {

                 'max_depth': [2, 5, 7, 9]
             }

clf = tree.DecisionTreeClassifier()

grid_clf = GridSearchCV(clf, param_grid, cv=10)

grid_clf.fit(X_train, y_train)
print(grid_clf.best_params_)



prediction = grid_clf.predict(X_test)

print(grid_clf.score(X_test, y_test))

#prediction


{'max_depth': 5}
0.5667074663402693


- Random Forest:

In [33]:
param_grid = {

                 'n_estimators': [5, 10, 15, 20, 25, 30],
                 'max_depth': [2, 5, 7, 9, 11, 13]
             }

clf = RandomForestClassifier()

grid_clf = GridSearchCV(clf, param_grid, cv=10)

grid_clf.fit(X_train, y_train)
print(grid_clf.best_params_)



prediction = grid_clf.predict(X_test)

print(grid_clf.score(X_test, y_test))

#prediction

{'max_depth': 5, 'n_estimators': 15}
0.6070991432068543


- Gaussian NB:

In [35]:
clf = GaussianNB()


#clf.fit(X_train, y_train)


scores = cross_val_score(clf, X_test, y_test, cv=10, scoring="accuracy")
print(scores)
meanScore = scores.mean()
print(meanScore)

#prediction = grid_clf.predict(X_test)

#print(grid_clf.score(X_test, y_test))

#prediction

[0.59756098 0.6097561  0.54878049 0.64634146 0.52439024 0.65853659
 0.62195122 0.55555556 0.62962963 0.56790123]
0.5960403492923818


- KNN:

In [36]:
param_grid = {

                 'n_neighbors': [1, 3, 5, 10, 15, 20, 25, 30, 35, 40, 45, 50]
             }

clf = KNeighborsClassifier()

grid_clf = GridSearchCV(clf, param_grid, cv=10)

grid_clf.fit(X_train, y_train)
print(grid_clf.best_params_)



prediction = grid_clf.predict(X_test)

print(grid_clf.score(X_test, y_test))

#prediction

{'n_neighbors': 50}
0.5777233782129743


- SGD Classifier:

In [37]:
param_grid = {

                 'alpha': [0, 0.1, 0.01, 0.001, 0.0001, 0.5, 0.05, 0.005, 0.005],
                 'max_iter': [1000]
             }

clf = linear_model.SGDClassifier()

grid_clf = GridSearchCV(clf, param_grid, cv=10)

grid_clf.fit(X_train, y_train)
print(grid_clf.best_params_)



prediction = grid_clf.predict(X_test)

print(grid_clf.score(X_test, y_test))

#prediction

{'alpha': 0.05, 'max_iter': 1000}
0.5813953488372093


/usr/local/lib/python3.10/dist-packages/sklearn/model_selection/_validation.py:540: FitFailedWarning: 
10 fits failed out of a total of 90.
The score on these train-test partitions for these parameters will be set to nan.
If these failures are not expected, you can try to debug them by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
10 fits failed with the following error:
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/sklearn/model_selection/_validation.py", line 888, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/usr/local/lib/python3.10/dist-packages/sklearn/base.py", line 1473, in wrapper
    return fit_method(estimator, *args, **kwargs)
  File "/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_stochastic_gradient.py", line 936, in fit
    self._more_validate_params()
  File "/usr/local/lib/python3.10

### Ensemble:

In [38]:
def ensemble_model(mod_1, mod_2, mod_3):
  joint = [mod_1[0], mod_2[0], mod_3[0]]
  print(joint)
  try:
    outcome = statistics.mode(joint)
  except:
    outcome = mod_1 # knn - best accuracy

  return outcome


### Simulation for Group Stage:

In [39]:
def simulation(n_simulations, groups, results, matches, X, y):


    for j in tqdm(range(n_simulations)):



        # model:

        X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=j) # random

        clf_3 = GaussianNB()
        clf_2 = RandomForestClassifier(max_depth = 7, n_estimators = 20)
        clf_1 = KNeighborsClassifier(n_neighbors = 35)
        #clf = GaussianNB()

        clf_1.fit(X_train, y_train)
        clf_2.fit(X_train, y_train)
        clf_3.fit(X_train, y_train)


        # GROUP STAGE:
        for group in groups:
            iterations = int(len(group)/2 + 1)
            winners = []

            print("\t \t \t {}".format(group))
            print("-----------------------------------------------------------------------")

            #matches = list(combinations(groups[group], 2))


            print(matches[group])
            print("\n")

            for match in matches[group]:
                home = match[0]
                away = match[1]
                print(home, away)


                # dataframe:
                df = pd.DataFrame(np.array([[np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan]]), columns=X_test.columns)

                #print(home)

                df['home_team_fifa_rank'] = home_team_df.loc[home, 'home_team_fifa_rank']
                df['home_team_total_fifa_points'] = home_team_df.loc[home, 'home_team_total_fifa_points']
                df['home_team_goalkeeper_score'] = home_team_df.loc[home, 'home_team_goalkeeper_score']
                df['home_team_mean_defense_score'] = home_team_df.loc[home, 'home_team_mean_defense_score']
                df['home_team_mean_offense_score'] = home_team_df.loc[home, 'home_team_mean_offense_score']
                df['home_team_mean_midfield_score'] = home_team_df.loc[home, 'home_team_mean_midfield_score']

                df['away_team_fifa_rank'] = away_team_df.loc[away, 'away_team_fifa_rank']
                df['away_team_total_fifa_points'] = away_team_df.loc[away, 'away_team_total_fifa_points']
                df['away_team_goalkeeper_score'] = away_team_df.loc[home, 'away_team_goalkeeper_score']
                df['away_team_mean_defense_score'] = away_team_df.loc[home, 'away_team_mean_defense_score']
                df['away_team_mean_offense_score'] = away_team_df.loc[home, 'away_team_mean_offense_score']
                df['away_team_mean_midfield_score'] = away_team_df.loc[home, 'away_team_mean_midfield_score']

                df['neutral_location'] = 1


                # predictions
                mod_1 = clf_1.predict(df)
                mod_2 = clf_2.predict(df)
                mod_3 = clf_3.predict(df)

                outcome = ensemble_model(mod_1, mod_2, mod_3)
                #print("Home Team Result: ", outcome)
                print(outcome)



                # update rankings: 0 = loss, 1 = draw, and 2 = win.

                if outcome == "Win":
                    winners.append(home)
                    idx = groups[group].index(home)
                    results[group][idx] += 3 / n_simulations
                    print("Winner:{} \n".format(home))


                if outcome == "Lose":
                    winners.append(away)
                    idx = groups[group].index(away)
                    results[group][idx] += 3 / n_simulations
                    print("Winner:{} \n".format(away))


                if outcome == "Draw":
                    winners.append("draw")
                    idx_home = groups[group].index(home)
                    results[group][idx_home] += 1 / n_simulations
                    idx_away = groups[group].index(away)
                    results[group][idx_away] += 1 / n_simulations
                    print("Winner: {} \n".format("Draw"))


                #print("\n")
                #print(winners)


    next_round = print_groups(groups, results)

    return next_round



def print_groups(groups, results):


    next_round = []
    for group in groups:


        #print(idx)


        print("-----------------------------------------------------------------------")
        print("\t \t \t {}".format(group))
        print("-----------------------------------------------------------------------")
        print("{:<1} \t {:<15} \t {:<15}".format("", "Team", "Points"))
        print("-----------------------------------------------------------------------")

        pos = 1
        while pos <= 4:
          #print(group)
          #print(group[idx])
          if pos == 5:
            pos = 10
            break

          idx = results[group].index(max(results[group]))
          print("{:<1} \t {:<15} \t {:<15}".format(pos, groups[group][idx], results[group][idx]))

          if pos == 1 or pos == 2:
            next_round.append(groups[group][idx])

          results[group].pop(idx)
          groups[group].pop(idx)
          pos += 1

    return next_round

### Simulation Knockout Stage:

In [40]:
def round_16(next_round):
  teams = []
  bracket = {"Part 1": [], "Part 2": []}
  i = 0
  while i < len(next_round):

    home = next_round[i]
    away = next_round[i + 3]
    bracket["Part 1"].append((home, away))
    teams.append(home)
    teams.append(away)

    home = next_round[i + 1]
    away = next_round[i + 2]
    bracket["Part 2"].append((home, away))
    teams.append(home)
    teams.append(away)

    i += 4

  return bracket, teams


In [41]:
def round_8(next_round):

  bracket = {"Part 1": [], "Part 2": []}
  i = 0
  while i < len(next_round):

    home = next_round[i]
    away = next_round[i + 1]
    bracket["Part 1"].append((home, away))

    home = next_round[i + 2]
    away = next_round[i + 3]
    bracket["Part 2"].append((home, away))

    i += 4

  return bracket

In [42]:
def semifinals(next_round):

    bracket = {"Part 1": [], "Part 2": []}

    home = next_round[0]
    away = next_round[2]
    bracket["Part 1"].append((home, away))

    home = next_round[1]
    away = next_round[3]
    bracket["Part 2"].append((home, away))


    return bracket


In [43]:
def final(next_round):

    bracket = {"Part 1": [], "Part 2": []}

    home = next_round[0]
    bracket["Part 1"].append(home)

    away = next_round[1]
    bracket["Part 2"].append(away)


    return bracket

In [44]:
def penalty_shootout(prob_home, prob_away):

  home = np.random.binomial(1, prob_home, 5)
  away = np.random.binomial(1, prob_away, 5)

  print("Penalty Shoot-Out:")
  print(home)
  print(away)

  if np.sum(home) >= np.sum(away):
    winner = 0
  else:
    winner = 1

  return winner

In [45]:
def print_bracket(round_16, winners_16, winners_8, winners_semis, winner_final):


  print("{:<15}--------                                                                                                                       --------{:<15}".format(round_16["Part 1"][0][0], round_16["Part 2"][0][0]))
  print("                       |                                                                                                           | ")
  print("                       |------- {:<15}                                                          {:<15} -------|              ".format(winners_16[0], winners_16[4]))
  print("                       |            |                                                                         |                                |")
  print("{:<15}--------             |                                                                                |                         --------{:<15}".format(round_16["Part 1"][0][1], round_16["Part 2"][0][1]))
  print("                                    |-------- {:<15}                       {:<15} --------|                         ".format(winners_8[0], winners_8[1]))
  print("{:<15}--------             |           |                                       |            |                          -------- {:<15}".format(round_16["Part 1"][1][0], round_16["Part 2"][1][0]))
  print("                       |            |           |                                       |            |           |")
  print("                       |------- {:<15} |                                       |                                      {:<15} -------|              ".format(winners_16[1], winners_16[5]))
  print("                       |                        |                                       |                        |                      ")
  print("{:<15}--------                         |                                       |                                       --------{:<15}".format(round_16["Part 1"][1][1], round_16["Part 2"][1][1]))

  print("                                                | -------- {:<15} {:<5} {:<15} -------- |                                     ".format(winners_semis[0] , "vs", winners_semis[1]))

  if winners_semis[0] == winner_final[0]:
    print("                                                               *     ")

  if winners_semis[1] == winner_final[0]:
    print("                                                                             *     ")


  print("{:<15}--------                         |                                       |                                       --------{:<15}".format(round_16["Part 1"][2][0], round_16["Part 2"][2][0]))
  print("                      |                         |                                       |                        | ")
  print("                      |------- {:<15}  |                                       |          {:<15} -------|              ".format(winners_16[2], winners_16[6]))
  print("                      |          |              |                                       |            |           |")
  print("{:<15}--------          |              |                                       |            |                          --------{:<15}".format(round_16["Part 1"][2][1], round_16["Part 2"][2][1]))
  print("                                 |-------- {:<15}                          {:<15} --------|                         ".format(winners_8[2], winners_8[3]))
  print("{:<15}--------          |                                                                    |                          --------{:<15}".format(round_16["Part 1"][3][0], round_16["Part 2"][3][0]))
  print("                      |          |                                                                  |           |")
  print("                      |------- {:<15}                                                           {:<15} -------|              ".format(winners_16[3], winners_16[7]))
  print("                      |                                                                                       |                      ")
  print("{:<15}--------                                                                                                               --------{:<15}".format(round_16["Part 1"][3][1], round_16["Part 2"][3][1]))


In [46]:
def simulation_knockout(n_simulations, X, y):




    teams_knockout =  {"Qatar":[0, 0, 0, 0, 0], "Ecuador":[0, 0, 0, 0, 0], "Senegal":[0, 0, 0, 0, 0], "Netherlands":[0, 0, 0, 0, 0], "IR Iran":[0, 0, 0, 0, 0], "Wales":[0, 0, 0, 0, 0], "USA":[0, 0, 0, 0, 0], "England":[0, 0, 0, 0, 0], "Argentina":[0, 0, 0, 0, 0], "Saudi Arabia":[0, 0, 0, 0, 0], "Mexico":[0, 0, 0, 0, 0], "Poland":[0, 0, 0, 0, 0], "France":[0, 0, 0, 0, 0], "Australia":[0, 0, 0, 0, 0], "Denmark":[0, 0, 0, 0, 0], "Tunisia":[0, 0, 0, 0, 0], "Spain":[0, 0, 0, 0, 0], "Germany":[0, 0, 0, 0, 0], "Costa Rica":[0, 0, 0, 0, 0], "Japan":[0, 0, 0, 0, 0], "Belgium":[0, 0, 0, 0, 0], "Canada":[0, 0, 0, 0, 0], "Morocco":[0, 0, 0, 0, 0], "Croatia":[0, 0, 0, 0, 0], "Morocco":[0, 0, 0, 0, 0], "Croatia":[0, 0, 0, 0, 0], "Brazil":[0, 0, 0, 0, 0], "Serbia":[0, 0, 0, 0, 0], "Switzerland":[0, 0, 0, 0, 0], "Cameroon":[0, 0, 0, 0, 0], "Portugal":[0, 0, 0, 0, 0], "Ghana":[0, 0, 0, 0, 0], "Uruguay":[0, 0, 0, 0, 0], "Korea Republic":[0, 0, 0, 0, 0]}



    for j in tqdm(range(n_simulations)):


        print("\t \t \t SIMULATION {}".format(j))
        print("-----------------------------------------------------------------------------------------------------------------------------------------------------------")

        groups = {"Group_A": ["Qatar", "Ecuador", "Senegal", "Netherlands"], "Group_B":["IR Iran", "Wales", "USA", "England"], "Group_C":["Argentina", "Saudi Arabia", "Mexico", "Poland"], "Group_D": ["France", "Australia", "Denmark", "Tunisia"], "Group_E": ["Spain", "Germany", "Costa Rica", "Japan"], "Group_F": ["Belgium", "Canada", "Morocco", "Croatia"], "Group_G": ["Brazil", "Serbia", "Switzerland", "Cameroon"], "Group_H": ["Portugal", "Ghana", "Uruguay", "Korea Republic"]}
        results = {"Group_A": [0,0,0,0], "Group_B":[0,0,0,0], "Group_C":[0,0,0,0], "Group_D": [0,0,0,0], "Group_E": [0,0,0,0], "Group_F": [0,0,0,0], "Group_G": [0,0,0,0], "Group_H": [0,0,0,0]}
        matches = {"Group_A": [("Qatar","Ecuador"),("Senegal","Netherlands"),("Qatar","Senegal"),("Netherlands","Ecuador"), ("Ecuador","Senegal"), ("Netherlands","Qatar")], "Group_B": [("England","IR Iran"),("USA","Wales"),("Wales","IR Iran"),("England","USA"), ("IR Iran","USA"), ("Wales","England")], "Group_C": [("Argentina","Saudi Arabia"),("Mexico","Poland"),("Poland","Saudi Arabia"),("Argentina","Mexico"), ("Poland","Argentina"), ("Saudi Arabia","Mexico")], "Group_D": [("Denmark","Tunisia"),("France","Australia"),("Tunisia","Australia"),("France","Denmark"), ("Tunisia","France"), ("Australia","Denmark")], "Group_E": [("Germany","Japan"),("Spain","Costa Rica"),("Japan","Costa Rica"),("Spain","Germany"), ("Japan","Spain"), ("Costa Rica","Germany")], "Group_F": [("Morocco","Croatia"),("Belgium","Canada"),("Belgium","Morocco"),("Croatia","Canada"), ("Croatia","Belgium"), ("Canada","Morocco")], "Group_G": [("Switzerland","Cameroon"),("Brazil","Serbia"),("Cameroon","Serbia"),("Brazil", "Switzerland"), ("Serbia","Switzerland"), ("Cameroon","Brazil")], "Group_H": [("Uruguay", "Korea Republic"),("Portugal","Ghana"),("Korea Republic", "Ghana"),("Portugal","Uruguay"),("Korea Republic","Portugal"), ("Ghana","Uruguay")]}


        # simulate GROUPS:
        next_round = simulation(1, groups, results, matches, X, y)
        bracket, teams16 = round_16(next_round)

        # model:

        X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=j) # random

        #clf = RandomForestClassifier(max_depth = 5, n_estimators = 20)
        clf = KNeighborsClassifier(n_neighbors = 45)

        clf.fit(X_train, y_train)


        # ROUND OF 16:

        print("\n")
        print("\t \t \t ROUND OF 16")
        print("-----------------------------------------------------------------------")

        winners_16 = []
        for part in bracket:





          print(bracket[part])
          print("\n")

          for match in bracket[part]:

            home = match[0]
            away = match[1]
            print(home, away)


            # dataframe:
            df = pd.DataFrame(np.array([[np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan]]), columns=X_test.columns)

            #print(home)

            df['home_team_fifa_rank'] = home_team_df.loc[home, 'home_team_fifa_rank']
            df['home_team_total_fifa_points'] = home_team_df.loc[home, 'home_team_total_fifa_points']
            df['home_team_goalkeeper_score'] = home_team_df.loc[home, 'home_team_goalkeeper_score']
            df['home_team_mean_defense_score'] = home_team_df.loc[home, 'home_team_mean_defense_score']
            df['home_team_mean_offense_score'] = home_team_df.loc[home, 'home_team_mean_offense_score']
            df['home_team_mean_midfield_score'] = home_team_df.loc[home, 'home_team_mean_midfield_score']

            df['away_team_fifa_rank'] = away_team_df.loc[away, 'away_team_fifa_rank']
            df['away_team_total_fifa_points'] = away_team_df.loc[away, 'away_team_total_fifa_points']
            df['away_team_goalkeeper_score'] = away_team_df.loc[home, 'away_team_goalkeeper_score']
            df['away_team_mean_defense_score'] = away_team_df.loc[home, 'away_team_mean_defense_score']
            df['away_team_mean_offense_score'] = away_team_df.loc[home, 'away_team_mean_offense_score']
            df['away_team_mean_midfield_score'] = away_team_df.loc[home, 'away_team_mean_midfield_score']

            df['neutral_location'] = 1

            # predictions
            outcome = clf.predict(df)
            probs = clf.predict_proba(df)

            if outcome == "Win":
                winners_16.append(home)
                print("Winner:{} \n".format(home))


            if outcome == "Lose":
                winners_16.append(away)
                print("Winner:{} \n".format(away))


            if outcome == "Draw":
                prob_home, prob_away = probs[0][0], probs[0][2]
                winner = penalty_shootout(prob_home, prob_away)
                if winner == 0:
                  winners_16.append(home)
                  print("Winner: {} \n".format(home))
                if winner == 1:
                  winners_16.append(away)
                  print("Winner: {} \n".format(away))




        # ROUND OF 8:

        print("\t \t \t ROUND OF 8")
        print("-----------------------------------------------------------------------")


        teams_8 = round_8(winners_16)
        print(teams_8)

        winners_8 = []
        for part in teams_8:


          print("\n")

          for match in teams_8[part]:

            home = match[0]
            away = match[1]
            print(home, away)


            # dataframe:
            df = pd.DataFrame(np.array([[np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan]]), columns=X_test.columns)

            #print(home)

            df['home_team_fifa_rank'] = home_team_df.loc[home, 'home_team_fifa_rank']
            df['home_team_total_fifa_points'] = home_team_df.loc[home, 'home_team_total_fifa_points']
            df['home_team_goalkeeper_score'] = home_team_df.loc[home, 'home_team_goalkeeper_score']
            df['home_team_mean_defense_score'] = home_team_df.loc[home, 'home_team_mean_defense_score']
            df['home_team_mean_offense_score'] = home_team_df.loc[home, 'home_team_mean_offense_score']
            df['home_team_mean_midfield_score'] = home_team_df.loc[home, 'home_team_mean_midfield_score']

            df['away_team_fifa_rank'] = away_team_df.loc[away, 'away_team_fifa_rank']
            df['away_team_total_fifa_points'] = away_team_df.loc[away, 'away_team_total_fifa_points']
            df['away_team_goalkeeper_score'] = away_team_df.loc[home, 'away_team_goalkeeper_score']
            df['away_team_mean_defense_score'] = away_team_df.loc[home, 'away_team_mean_defense_score']
            df['away_team_mean_offense_score'] = away_team_df.loc[home, 'away_team_mean_offense_score']
            df['away_team_mean_midfield_score'] = away_team_df.loc[home, 'away_team_mean_midfield_score']

            df['neutral_location'] = 1

            # predictions
            outcome = clf.predict(df)
            probs = clf.predict_proba(df)

            if outcome == "Win":
                winners_8.append(home)
                print("Winner:{} \n".format(home))


            if outcome == "Lose":
                winners_8.append(away)
                print("Winner:{} \n".format(away))


            if outcome == "Draw":
                prob_home, prob_away = probs[0][0], probs[0][2]
                winner = penalty_shootout(prob_home, prob_away)
                if winner == 0:
                  winners_8.append(home)
                  print("Winner: {} \n".format(home))
                if winner == 1:
                  winners_8.append(away)
                  print("Winner: {} \n".format(away))



        # SEMI-FINALS:

        print("\t \t \t SEMIFINALS")
        print("-----------------------------------------------------------------------")

        teams_semis = semifinals(winners_8)

        winners_semis = []
        for part in teams_semis:

          print("\n")

          for match in teams_semis[part]:

            home = match[0]
            away = match[1]
            print(home, away)


            # dataframe:
            df = pd.DataFrame(np.array([[np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan]]), columns=X_test.columns)

            #print(home)

            df['home_team_fifa_rank'] = home_team_df.loc[home, 'home_team_fifa_rank']
            df['home_team_total_fifa_points'] = home_team_df.loc[home, 'home_team_total_fifa_points']
            df['home_team_goalkeeper_score'] = home_team_df.loc[home, 'home_team_goalkeeper_score']
            df['home_team_mean_defense_score'] = home_team_df.loc[home, 'home_team_mean_defense_score']
            df['home_team_mean_offense_score'] = home_team_df.loc[home, 'home_team_mean_offense_score']
            df['home_team_mean_midfield_score'] = home_team_df.loc[home, 'home_team_mean_midfield_score']

            df['away_team_fifa_rank'] = away_team_df.loc[away, 'away_team_fifa_rank']
            df['away_team_total_fifa_points'] = away_team_df.loc[away, 'away_team_total_fifa_points']
            df['away_team_goalkeeper_score'] = away_team_df.loc[home, 'away_team_goalkeeper_score']
            df['away_team_mean_defense_score'] = away_team_df.loc[home, 'away_team_mean_defense_score']
            df['away_team_mean_offense_score'] = away_team_df.loc[home, 'away_team_mean_offense_score']
            df['away_team_mean_midfield_score'] = away_team_df.loc[home, 'away_team_mean_midfield_score']

            df['neutral_location'] = 1

            # predictions
            outcome = clf.predict(df)
            probs = clf.predict_proba(df)

            if outcome == "Win":
                winners_semis.append(home)
                print("Winner:{} \n".format(home))


            if outcome == "Lose":
                winners_semis.append(away)
                print("Winner:{} \n".format(away))


            if outcome == "Draw":
                prob_home, prob_away = probs[0][0], probs[0][2]
                winner = penalty_shootout(prob_home, prob_away)
                if winner == 0:
                  winners_semis.append(home)
                  print("Winner: {} \n".format(home))
                if winner == 1:
                  winners_semis.append(away)
                  print("Winner: {} \n".format(away))




        # FINAL:

        print("\t \t \t FINAL")
        print("-----------------------------------------------------------------------")

        teams_final = final(winners_semis)


        winner_final = []



        print("\n")


        home = teams_final["Part 1"][0]
        away = teams_final["Part 2"][0]
        print(home, away)


        # dataframe:
        df = pd.DataFrame(np.array([[np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan]]), columns=X_test.columns)

        #print(home)

        df['home_team_fifa_rank'] = home_team_df.loc[home, 'home_team_fifa_rank']
        df['home_team_total_fifa_points'] = home_team_df.loc[home, 'home_team_total_fifa_points']
        df['home_team_goalkeeper_score'] = home_team_df.loc[home, 'home_team_goalkeeper_score']
        df['home_team_mean_defense_score'] = home_team_df.loc[home, 'home_team_mean_defense_score']
        df['home_team_mean_offense_score'] = home_team_df.loc[home, 'home_team_mean_offense_score']
        df['home_team_mean_midfield_score'] = home_team_df.loc[home, 'home_team_mean_midfield_score']

        df['away_team_fifa_rank'] = away_team_df.loc[away, 'away_team_fifa_rank']
        df['away_team_total_fifa_points'] = away_team_df.loc[away, 'away_team_total_fifa_points']
        df['away_team_goalkeeper_score'] = away_team_df.loc[home, 'away_team_goalkeeper_score']
        df['away_team_mean_defense_score'] = away_team_df.loc[home, 'away_team_mean_defense_score']
        df['away_team_mean_offense_score'] = away_team_df.loc[home, 'away_team_mean_offense_score']
        df['away_team_mean_midfield_score'] = away_team_df.loc[home, 'away_team_mean_midfield_score']

        df['neutral_location'] = 1

        # predictions
        outcome = clf.predict(df)
        probs = clf.predict_proba(df)

        if outcome == "Win":
            winner_final.append(home)
            print("Winner:{} \n".format(home))


        if outcome == "Lose":
            winner_final.append(away)
            print("Winner:{} \n".format(away))


        if outcome == "Draw":
            prob_home, prob_away = probs[0][0], probs[0][2]
            winner = penalty_shootout(prob_home, prob_away)
            if winner == 0:
              winner_final.append(home)
              print("Winner: {} \n".format(home))
            if winner == 1:
              winner_final.append(away)
              print("Winner: {} \n".format(away))




        # store results:

        for country in teams16:
          teams_knockout[country][0] += 1

        for country in winners_16:
          teams_knockout[country][1] += 1

        for country in winners_8:
          teams_knockout[country][2] += 1

        for country in winners_semis:
          teams_knockout[country][3] += 1

        teams_knockout[winner_final[0]][4] += 1

        print_bracket(bracket, winners_16, winners_8, winners_semis, winner_final)



    for team in teams_knockout:
      for i in range(len(teams_knockout[team])):
        teams_knockout[team][i] /= n_simulations

    print("\n")
    print("PROBABILITIES OF EACH TEAM: \n")
    print("Round of 16 / Round of 8 / Semifinals / Final / Win")
    print(teams_knockout)

    return winner_final[0]

# Simulation:

In [47]:
simulation_knockout(250, X, y)

  0%|          | 0/250 [00:00<?, ?it/s]

	 	 	 SIMULATION 0
-----------------------------------------------------------------------------------------------------------------------------------------------------------



  0%|          | 0/1 [00:00<?, ?it/s]

	 	 	 Group_A
-----------------------------------------------------------------------
[('Qatar', 'Ecuador'), ('Senegal', 'Netherlands'), ('Qatar', 'Senegal'), ('Netherlands', 'Ecuador'), ('Ecuador', 'Senegal'), ('Netherlands', 'Qatar')]


Qatar Ecuador
['Lose', 'Win', 'Lose']
Lose
Winner:Ecuador 

Senegal Netherlands
['Win', 'Lose', 'Lose']
Lose
Winner:Netherlands 

Qatar Senegal
['Win', 'Win', 'Lose']
Win
Winner:Qatar 

Netherlands Ecuador
['Draw', 'Win', 'Draw']
Draw
Winner: Draw 

Ecuador Senegal
['Win', 'Win', 'Win']
Win
Winner:Ecuador 

Netherlands Qatar
['Win', 'Win', 'Win']
Win
Winner:Netherlands 

	 	 	 Group_B
-----------------------------------------------------------------------
[('England', 'IR Iran'), ('USA', 'Wales'), ('Wales', 'IR Iran'), ('England', 'USA'), ('IR Iran', 'USA'), ('Wales', 'England')]


England IR Iran
['Win', 'Lose', 'Draw']
Win
Winner:England 

USA Wales
['Draw', 'Win', 'Draw']
Draw
Winner: Draw 

Wales IR Iran
['Win', 'Win', 'Win']
Win
Winner:Wales 

En


100%|██████████| 1/1 [00:00<00:00,  1.30it/s]

...

['Win', 'Win', 'Draw']
Win
Winner:Korea Republic 

Portugal Uruguay
['Win', 'Win', 'Lose']
Win
Winner:Portugal 

Korea Republic Portugal
['Lose', 'Win', 'Lose']
Lose
Winner:Portugal 

Ghana Uruguay
['Lose', 'Win', 'Lose']
Lose
Winner:Uruguay 

-----------------------------------------------------------------------
	 	 	 Group_A
-----------------------------------------------------------------------
  	 Team            	 Points         
-----------------------------------------------------------------------
1 	 Ecuador         	 7.0            
2 	 Netherlands     	 7.0            
3 	 Qatar           	 3.0            
4 	 Senegal         	 0              
-----------------------------------------------------------------------
	 	 	 Group_B
-----------------------------------------------------------------------
  	 Team            	 Points         
-----------------------------------------------------------------------
1 	 England         	 7.0            
2 	 USA             	 5.0     

Winner:Ecuador 

Mexico Denmark
Winner:Mexico 

Germany Croatia
Winner:Germany 

Switzerland Uruguay
Winner:Switzerland 

[('Netherlands', 'England'), ('Argentina', 'France'), ('Spain', 'Belgium'), ('Brazil', 'Portugal')]


Netherlands England
Winner:England 

Argentina France
Winner:Argentina 

Spain Belgium
Winner:Spain 

Brazil Portugal
Winner:Brazil 

	 	 	 ROUND OF 8
-----------------------------------------------------------------------
{'Part 1': [('Ecuador', 'Mexico'), ('England', 'Argentina')], 'Part 2': [('Germany', 'Switzerland'), ('Spain', 'Brazil')]}


Ecuador Mexico
Penalty Shoot-Out:
[1 0 0 0 0]
[1 0 1 0 0]
Winner: Mexico 

England Argentina


100%|██████████| 250/250 [05:25<00:00,  1.30s/it]

Winner:Argentina 



Germany Switzerland
Winner:Germany 

Spain Brazil
Winner:Spain 

	 	 	 SEMIFINALS
-----------------------------------------------------------------------


Mexico Germany
Winner:Germany 



Argentina Spain
Winner:Argentina 

	 	 	 FINAL
-----------------------------------------------------------------------


Germany Argentina
Winner:Germany 

Ecuador        --------                                                                                                                       --------Netherlands    
                       |                                                                                                           | 
                       |------- Ecuador                                                                  England         -------|              
                       |            |                                                                         |                                |
USA            --------             |       

'Germany'